In [62]:
import pandas as pd
import numpy as np
import tensorflow as tf
from os import listdir
from sklearn.model_selection import train_test_split
print ('The version of TensorFlow is {}'.format(tf.__version__))

The version of TensorFlow is 1.4.0


## Load data from ASRS database

In [63]:
root_path = './data'

appended_data = []
for file_name in listdir(root_path):
    file_path = root_path + '/' + file_name.encode().decode('utf-8')
    data_from_one_csv = pd.read_csv(file_path, skiprows=1)
    appended_data.append(data_from_one_csv)
    
data = pd.concat(appended_data, axis=0)
data = data.drop(columns = ['ACN', 'Date', 'Local Time Of Day', 'Ceiling', 'Callback', 'Callback.1', 'Unnamed: 96'])
data = data.rename(index=str, columns={"Flight Phase": "Flight Phase1"})

## remove the rows with empty synopsis description
data = data[pd.notnull(data['Synopsis'])]

X = data.drop(columns = 'Result')
Y_raw = pd.DataFrame(data['Result'])

processed_Y = []
for index, row in Y_raw.iterrows():
    #print (index, row['Result'])
    outcome = row['Result']
    if type(outcome) == np.float:
        res = 'unknown'
        processed_Y.append(res)
    elif ';' in outcome:
        res = str(outcome).split(';')[0]
        processed_Y.append(res)
    else:
        res = outcome
        processed_Y.append(res)

Y = pd.DataFrame(processed_Y, columns = ['Result'])

#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~ Single file process ~~~~~~~~~~~~~~~~~~~~~~~~
#~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
# file_name = 'ASRS_DBOnline.csv'
# data = pd.read_csv(file_name)
# data = data.drop(columns = ['ACN', 'Date', 'Local Time Of Day', 'Ceiling', 'Callback', 'Callback.1'])
# X = data.drop(columns = 'Result')
# Y = data['Result']

# for i in range(Y.shape[0]):
#     if ';' in str(Y[i]):
#         Y.set_value(i, Y[i].split(';')[0])
#     elif Y[i] is np.nan:
#         Y.set_value(i, 'unknown')

In [64]:
Y.shape

(64573, 1)

In [65]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
Y = pd.DataFrame(le.fit_transform(Y), index = X.index)
        
n_classes = int(Y.max()[0]) + 1

c:\anaconda\pkgs\python-3.6.3-h9e2ca53_1\lib\site-packages\sklearn\preprocessing\label.py:111: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [66]:
## change column names
new_col_name = []
for col in X.columns:
    #print(type(col))
    new_col_name.append(col.replace('/ ', '').replace(' ', '_'))
    
X.columns = new_col_name

## output the headers from the csv file
X.keys()

Index(['Locale_Reference', 'State_Reference', 'Relative_Position.Angle.Radial',
       'Relative_Position.Distance.Nautical_Miles',
       'Altitude.AGL.Single_Value', 'Altitude.MSL.Single_Value',
       'Flight_Conditions', 'Weather_Elements_Visibility',
       'Work_Environment_Factor', 'Light', 'RVR.Single_Value', 'ATC_Advisory',
       'Aircraft_Operator', 'Make_Model_Name', 'Aircraft_Zone', 'Crew_Size',
       'Operating_Under_FAR_Part', 'Flight_Plan', 'Mission', 'Nav_In_Use',
       'Flight_Phase1', 'Route_In_Use', 'Airspace',
       'Maintenance_Status.Maintenance_Deferred',
       'Maintenance_Status.Records_Complete',
       'Maintenance_Status.Released_For_Service',
       'Maintenance_Status.Required_Correct_Doc_On_Board',
       'Maintenance_Status.Maintenance_Type',
       'Maintenance_Status.Maintenance_Items_Involved', 'Cabin_Lighting',
       'Number_Of_Seats.Number', 'Passengers_On_Board.Number',
       'Crew_Size_Flight_Attendant.Number_Of_Crew', 'Aircraft_Component',

## Output the data types of all the items

In [67]:
data_type = []
for item_name in X.keys():
    data_type.append(type(X[item_name][0]))

print ('\n')
print ('~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~')
print ('The unique data types across all the items are:', set(data_type))
print ('~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~')



~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
The unique data types across all the items are: {<class 'numpy.float64'>, <class 'float'>, <class 'str'>}
~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~


## Count the number of missing values in each attribute

In [68]:
for item_name in X.keys():
    ## find the number of NaN in this item
    no = np.sum(X[item_name].isna().astype(int))
    #print ('The number of {} with value equal to NaN is {}'.format(item_name, no))
    
    ## Replace the missing value with corresponding values
    if no > 0:
        if type(X[item_name][0]) == np.float64:
            X[item_name].fillna(-1, inplace = True)
        else:
            X[item_name].fillna('unknown', inplace = True)
X['Crew_Size'].head()

0    2.0
1    2.0
2    2.0
3    2.0
4    2.0
Name: Crew_Size, dtype: float64

## Latent Dirichlet Allocation --> Train LDA Model

In [ ]:
#########################################################
#############   Latent Dirichlet Allocation   ###########
#########################################################
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.porter import PorterStemmer
from nltk.stem import WordNetLemmatizer
from gensim import corpora
import gensim
import string

tokenizer = RegexpTokenizer(r'\w+')

# create English stop words list
stop_words = stopwords.words('english') + list(string.punctuation)

# Create p_stemmer of class PorterStemmer
p_stemmer = SnowballStemmer('english')
wordnet_lemmatizer = PorterStemmer()

df = X

texts = []
index = df.columns.get_loc("Synopsis")

for i in range(df.shape[0]):
    if type(df.iloc[i, index]) is str:
         # clean and tokenize document string
        raw = df.iloc[i, index].lower()

        tokens = tokenizer.tokenize(raw)

        # remove stop words from tokens
        stopped_tokens = [i for i in tokens if not i in stop_words]

        # stem tokens
        stemmed_tokens = [wordnet_lemmatizer.stem(i) for i in stopped_tokens]

        # add tokens to list
        texts.append(stemmed_tokens)

# turn the tokenized documents into a id <-> term dictionary
dictionary = corpora.Dictionary(texts)
    
# convert tokenized documents into a document-term matrix
corpus = [dictionary.doc2bow(text) for text in texts]


num_words = 6
num_topics = 200

# generate LDA model
ldamodel = gensim.models.ldamodel.LdaModel(corpus, num_topics = num_topics, id2word = dictionary, 
                                           distributed = False, passes=20, eval_every=10)

topics = ldamodel.print_topics(num_topics = num_topics, num_words = num_words)

c:\anaconda\pkgs\python-3.6.3-h9e2ca53_1\lib\site-packages\gensim\models\ldamodel.py:802: RuntimeWarning: divide by zero encountered in log
  diff = np.log(self.expElogbeta)


## Trained LDA model used to mine topics for each document

In [ ]:
import re
topic_words = []
all_topics = []
document_no = df.shape[0]
for i in range(document_no):
    doc_ID = i
    topics_document= ldamodel.get_document_topics(dictionary.doc2bow(texts[doc_ID]))
    print ('~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~')
    print (df.iloc[doc_ID, index].lower())
    #print (topics_document)
    #print ('\n')

    
    topic_with_max_prob = max(topics_document, key=lambda item: item[1])
    topic_ID, document_topics = topics[topic_with_max_prob[0]][0], topics[topic_with_max_prob[0]][1]
    prob = topic_with_max_prob[1]
    print ('\n')
    print ('Topics mined from the synopsis:')
    print (document_topics, ' --- with prob:', topic_with_max_prob[1])
    
    list_words = []
    quoted = re.compile('"[^"]*"')
    for value in quoted.findall(document_topics):
        list_words.append(value.replace('"',''))
        topic_words.append(value.replace('"',''))
    
    all_topics.append(list_words)

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
an a320 with duel lgciu failures executed a gar and working with maint was able to recover ctl. an emer was declared.


Topics mined from the synopsis:
0.313*"execut" + 0.256*"wing" + 0.143*"mid" + 0.104*"vor" + 0.065*"top" + 0.029*"apch"  --- with prob: 0.1542308
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a320 experienced conflict with unrpted heli while on final for rwy 18r at dfw.


Topics mined from the synopsis:
0.328*"took" + 0.157*"test" + 0.111*"piper" + 0.110*"forc" + 0.073*"loop" + 0.063*"airplan"  --- with prob: 0.3005
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a b737-300 crew encountered a 20 second severe turb upset with flt attendants and pax seated.


Topics mined from the synopsis:
0.525*"attend" + 0.108*"seat" + 0.094*"board" + 0.085*"agent" + 0.062*"far" + 0.062*"cabin"  --- with prob: 0.22128986
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a t38 plt in formation discusses a stuck mike on lead acft's atc radio. altdev results as wingman notifies lead of radio prob.


Topics mined from the synopsis:
0.267*"short" + 0.259*"line" + 0.225*"hold" + 0.079*"aviat" + 0.030*"discuss" + 0.020*"acknowledg"  --- with prob: 0.18083507
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a b757; on tkof roll; had its r eng fail. aborted tkof at 110 kts. eng failure caused by failed coupling clamp on fuel flow governor.


Topics mined from the synopsis:
0.519*"roll" + 0.088*"r" + 0.073*"flow" + 0.060*"50" + 0.056*"40" + 0.035*"button"  --- with prob: 0.39598495
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a drunk pax acted belligerently toward the flt attendants and was arrested upon arr at jfk.


Topics mined from the synopsis:
0.196*"closur" + 0.156*"32" + 0.127*"rapidli" + 0.091*"advanc" + 0.078*"act" + 0.057*"arrest"  --- with p

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
c177 in tfc pattern at cma experienced conflict after an atc directed turn to base leg followed by additional questionable atc actions.


Topics mined from the synopsis:
0.369*"conflict" + 0.218*"vfr" + 0.210*"advis" + 0.044*"proxim" + 0.041*"eventu" + 0.017*"pdx"  --- with prob: 0.14806837
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a distracted vfr pa32 plt violated class 'c' airspace after losing situational awareness because of a phone call to fss concerning his expired ete.


Topics mined from the synopsis:
0.261*"rout" + 0.187*"situat" + 0.118*"c" + 0.115*"violat" + 0.105*"lose" + 0.084*"awar"  --- with prob: 0.29441178
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
zdc ctlr experienced operror at fl360 when incorrect alt assignment readback was missed.


Topics mined from the synopsis:
0.612*"issu" + 0.093*"vicin" + 0.079*"realiz" + 0.067*"standard" + 0.028*"give" + 0

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
emb135 capt on the ramp at bos takes evasive action to avoid collision with quick moving acft pushing back.


Topics mined from the synopsis:
0.229*"action" + 0.169*"collis" + 0.160*"shortli" + 0.132*"evas" + 0.083*"inbound" + 0.066*"avoid"  --- with prob: 0.40033334
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
atr72 crew taxied around an a300 at sju to access the ramp.


Topics mined from the synopsis:
0.431*"taxi" + 0.201*"ramp" + 0.095*"weight" + 0.077*"safeti" + 0.075*"sign" + 0.045*"entri"  --- with prob: 0.25358057
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
sport plt at top experiences nmac when commencing a gar.


Topics mined from the synopsis:
0.313*"execut" + 0.256*"wing" + 0.143*"mid" + 0.104*"vor" + 0.065*"top" + 0.029*"apch"  --- with prob: 0.250625
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a pa28 plt flying ils apch to rdu mis-progr

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
b737 flt crew with zla at fl250 described conflict with opposite direction tfc and responded to tcas ra preventing a loss of legal separation.


Topics mined from the synopsis:
0.289*"loss" + 0.268*"describ" + 0.228*"separ" + 0.055*"result" + 0.050*"incid" + 0.022*"caus"  --- with prob: 0.16694444
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
b737 flt crew during ils apch elects to perform a gar due to unstable apch.


Topics mined from the synopsis:
0.313*"execut" + 0.256*"wing" + 0.143*"mid" + 0.104*"vor" + 0.065*"top" + 0.029*"apch"  --- with prob: 0.25041667
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
b737 at fl200 with zla experienced tcas ra after an atc directed dscnt.


Topics mined from the synopsis:
0.292*"jet" + 0.285*"ra" + 0.252*"tca" + 0.070*"crew" + 0.043*"driver" + 0.017*"acr"  --- with prob: 0.26017138
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~

...

0.612*"return" + 0.156*"unabl" + 0.063*"went" + 0.032*"got" + 0.030*"experienc" + 0.021*"overheat"  --- with prob: 0.12531249
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
pilot alleged the engine failure procedure off runway 4 in avp is unsafe and does not provide adequate terrain clearance.


Topics mined from the synopsis:
0.502*"procedur" + 0.079*"odor" + 0.068*"smell" + 0.061*"burn" + 0.058*"strong" + 0.057*"poor"  --- with prob: 0.09136364
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a giv failed to make a crossing restriction on approach to teb when the chief pilot in the right seat advised incorrectly it was not necessary.


Topics mined from the synopsis:
0.411*"restrict" + 0.201*"extend" + 0.064*"slat" + 0.046*"contain" + 0.041*"60" + 0.038*"fail"  --- with prob: 0.10624064
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
zmp controller described event when aircraft requested lower altitude without stating reason

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
emb190 first officer reports contact with tug while being marshaled into gate. marshaller was paying attention to stop line and not to proximity of tug; which had been positioned for outbound push.


Topics mined from the synopsis:
0.547*"il" + 0.095*"nav" + 0.089*"marshal" + 0.075*"loc" + 0.055*"said" + 0.033*"mi"  --- with prob: 0.117941186
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
b747 crew is informed by flight attendant of overheated panel and electrical fumes in aft galley. utility bus eicas message appears shortly thereafter. emergency declared and flight returns to departure airport.


Topics mined from the synopsis:
0.187*"descent" + 0.180*"right" + 0.170*"emerg" + 0.118*"initi" + 0.103*"declar" + 0.082*"crew"  --- with prob: 0.10887128
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a320 flight crew refuses aircraft for surge tank fuel leaks which have not been ad

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
an fa50 captain reported that his request for the normal obstacle departure procedure at hnd was denied because of las traffic concerns. the substitute procedure involved visual terrain clearance which could be potentially unsafe at night.


Topics mined from the synopsis:
0.502*"procedur" + 0.079*"odor" + 0.068*"smell" + 0.061*"burn" + 0.058*"strong" + 0.057*"poor"  --- with prob: 0.10552632
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a single engine pilot reports a nmac at gnv with traffic that he failed to identify as atc assigned preceding traffic because he thought atc identified third aircraft on short final was number one and he was therefore number two.


Topics mined from the synopsis:
0.644*"atc" + 0.196*"vector" + 0.047*"toward" + 0.027*"preced" + 0.026*"wait" + 0.010*"n90"  --- with prob: 0.13659091
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a crj-700 crew ab

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
sf34 experiences altitude excursion as the result of accepting clearance for another flight with a similar call sign.


Topics mined from the synopsis:
0.668*"altitud" + 0.079*"assign" + 0.071*"fatigu" + 0.047*"crew" + 0.045*"result" + 0.025*"fals"  --- with prob: 0.14974923
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
a319 suffers bird strike on take off.


Topics mined from the synopsis:
0.358*"take" + 0.280*"md" + 0.211*"anomali" + 0.027*"mlg" + 0.015*"mco" + 0.015*"unannounc"  --- with prob: 0.1675
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
captain reports distractions caused by raas announcements covering atc transmissions during potential runway incursion risk from another aircraft awaiting a takeoff clearance.


Topics mined from the synopsis:
0.463*"final" + 0.141*"avoid" + 0.100*"instrument" + 0.041*"creat" + 0.033*"either" + 0.030*"slc"  --- with prob: 0.0924144

~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
crj700 flight crew descends below their clearance altitude before ils glide slope capture on an ils approach.


Topics mined from the synopsis:
0.547*"il" + 0.095*"nav" + 0.089*"marshal" + 0.075*"loc" + 0.055*"said" + 0.033*"mi"  --- with prob: 0.25062498
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
an a320 first officer reports an egpws 'pull up' alert during a day vmc visual approach to las runway 1r. he had difficulty determining the aircraft's height above the terrain visually.


Topics mined from the synopsis:
0.264*"receiv" + 0.208*"warn" + 0.188*"alert" + 0.115*"crew" + 0.095*"terrain" + 0.045*"gpw"  --- with prob: 0.117941186
~~~~~~~~~~~~~~~~~~~~ The original synopsis report  ~~~~~~~~~~~~~~~~
flight crew of small turbojet transport fails to remain east of ord 345 radial on pal-waukee 2 sid from pwk.


Topics mined from the synopsis:
0.318*"prior" + 0.169*"sid" + 0.119*"crew" + 0.112*"prog

In [ ]:
import numpy as np

topic_rep = np.zeros(shape = (df.shape[0], num_words))
unique_topic_words = list(set(topic_words))

i = 0
for doc_topic in all_topics:
    for j in range(len(doc_topic)):
        loc = unique_topic_words.index(doc_topic[j])
        topic_rep[i, j] = loc
    i = i + 1
    
topic_rep

X['word_1'] = topic_rep[:, 0]
X['word_2'] = topic_rep[:, 1]
X['word_3'] = topic_rep[:, 2]
X['word_4'] = topic_rep[:, 3]
X['word_5'] = topic_rep[:, 4]
X['word_6'] = topic_rep[:, 5]
X.head()

## Construct feature columns

In [ ]:
## Location
Locale_Reference = tf.feature_column.categorical_column_with_hash_bucket('Locale_Reference', 
                                                                         hash_bucket_size = len(set(X['Locale_Reference'])))
State_Reference = tf.feature_column.categorical_column_with_hash_bucket('State_Reference', 
                                                                        hash_bucket_size = len(set(X['State_Reference'])))


## Environment
Flight_Conditions = tf.feature_column.categorical_column_with_hash_bucket('Flight_Conditions', 
                                                                hash_bucket_size = len(set(X['State_Reference'])))
Weather_Elements_Visibility = tf.feature_column.categorical_column_with_hash_bucket('Weather_Elements_Visibility', 
                                                            hash_bucket_size = len(set(X['Weather_Elements_Visibility'])))
Work_Environment_Factor = tf.feature_column.categorical_column_with_hash_bucket('Work_Environment_Factor', 
                                                            hash_bucket_size = len(set(X['Work_Environment_Factor'])))
Light = tf.feature_column.categorical_column_with_hash_bucket('Light', hash_bucket_size = len(set(X['Work_Environment_Factor'])))


## Aircraft
ATC_Advisory = tf.feature_column.categorical_column_with_hash_bucket('ATC_Advisory', 
                                                            hash_bucket_size = len(set(X['ATC_Advisory'])))
Aircraft_Operator = tf.feature_column.categorical_column_with_hash_bucket('Aircraft_Operator', 
                                                                hash_bucket_size = len(set(X['Aircraft_Operator'])))
Make_Model_Name = tf.feature_column.categorical_column_with_hash_bucket('Make_Model_Name', 
                                                            hash_bucket_size = len(set(X['Make_Model_Name'])))
Crew_Size = tf.feature_column.numeric_column('Crew_Size', [1])
Flight_Plan = tf.feature_column.categorical_column_with_hash_bucket('Flight_Plan', 
                                                            hash_bucket_size = len(set(X['Flight_Plan'])))
Mission = tf.feature_column.categorical_column_with_hash_bucket('Mission', 
                                                                hash_bucket_size = len(set(X['Mission'])))
Flight_Phase1 = tf.feature_column.categorical_column_with_hash_bucket('Flight_Phase1', 
                                                                      hash_bucket_size = len(set(X['Flight_Phase1'])))
Route_In_Use = tf.feature_column.categorical_column_with_hash_bucket('Route_In_Use', 
                                                                     hash_bucket_size = len(set(X['Route_In_Use'])))
Airspace = tf.feature_column.categorical_column_with_hash_bucket('Airspace', 
                                                                 hash_bucket_size = len(set(X['Airspace'])))

## Component
Aircraft_Component = tf.feature_column.categorical_column_with_hash_bucket('Aircraft_Component', 
                                                             hash_bucket_size = len(set(X['Aircraft_Component'])))
Manufacturer = tf.feature_column.categorical_column_with_hash_bucket('Manufacturer', 
                                                        hash_bucket_size = len(set(X['Manufacturer'])))

## Person
Location_Of_Person = tf.feature_column.categorical_column_with_hash_bucket('Location_Of_Person', 
                                                                hash_bucket_size = len(set(X['Location_Of_Person'])))
Location_In_Aircraft = tf.feature_column.categorical_column_with_hash_bucket('Location_In_Aircraft',
                                                            hash_bucket_size = len(set(X['Location_In_Aircraft'])))
Reporter_Organization = tf.feature_column.categorical_column_with_hash_bucket('Reporter_Organization',
                                                            hash_bucket_size = len(set(X['Reporter_Organization'])))
Function = tf.feature_column.categorical_column_with_hash_bucket('Function', hash_bucket_size = len(set(X['Function'])))
Qualification = tf.feature_column.categorical_column_with_hash_bucket('Qualification', 
                                                                      hash_bucket_size = len(set(X['Qualification'])))
Human_Factors = tf.feature_column.categorical_column_with_hash_bucket('Human_Factors', 
                                                                      hash_bucket_size = len(set(X['Human_Factors'])))

## Events
Anomaly = tf.feature_column.categorical_column_with_hash_bucket('Anomaly', 
                                                                hash_bucket_size = len(set(X['Anomaly'])))
Detector = tf.feature_column.categorical_column_with_hash_bucket('Detector', 
                                                                 hash_bucket_size = len(set(X['Detector'])))
When_Detected = tf.feature_column.categorical_column_with_hash_bucket('When_Detected', 
                                                                      hash_bucket_size = len(set(X['When_Detected'])))
Were_Passengers_Involved_In_Event = tf.feature_column.categorical_column_with_hash_bucket('Were_Passengers_Involved_In_Event',
                                                    hash_bucket_size = len(set(X['Were_Passengers_Involved_In_Event'])))

## Assessments
Contributing_Factors_Situations = tf.feature_column.categorical_column_with_hash_bucket('Contributing_Factors_Situations', 
                                                   hash_bucket_size = len(set(X['Contributing_Factors_Situations'])))
Primary_Problem = tf.feature_column.categorical_column_with_hash_bucket('Primary_Problem', 
                                                        hash_bucket_size = len(set(X['Primary_Problem'])))


## Topic Mining from Accident Synopsis
word_1 = tf.feature_column.categorical_column_with_hash_bucket('word_1', hash_bucket_size = len(unique_topic_words))
word_2 = tf.feature_column.categorical_column_with_hash_bucket('word_2', hash_bucket_size = len(unique_topic_words))
word_3 = tf.feature_column.categorical_column_with_hash_bucket('word_3', hash_bucket_size = len(unique_topic_words))
word_4 = tf.feature_column.categorical_column_with_hash_bucket('word_4', hash_bucket_size = len(unique_topic_words))
word_5 = tf.feature_column.categorical_column_with_hash_bucket('word_5', hash_bucket_size = len(unique_topic_words))
word_6 = tf.feature_column.categorical_column_with_hash_bucket('word_6', hash_bucket_size = len(unique_topic_words))

In [ ]:
## Place
Locale_Reference = tf.feature_column.embedding_column(Locale_Reference, len(set(X['Locale_Reference'])))
State_Reference = tf.feature_column.embedding_column(State_Reference, len(set(X['State_Reference'])))


## Environment
Flight_Conditions = tf.feature_column.embedding_column(Flight_Conditions,  len(set(X['Flight_Conditions'])))
Weather_Elements_Visibility = tf.feature_column.embedding_column(Weather_Elements_Visibility,  
                                                                 len(set(X['Weather_Elements_Visibility'])))
Work_Environment_Factor = tf.feature_column.embedding_column(Work_Environment_Factor,  len(set(X['Work_Environment_Factor'])))
Light = tf.feature_column.embedding_column(Light, len(set(X['Light'])))


## Aircraft
ATC_Advisory = tf.feature_column.embedding_column(ATC_Advisory, len(set(X['ATC_Advisory'])))
Aircraft_Operator = tf.feature_column.embedding_column(Aircraft_Operator, len(set(X['Aircraft_Operator'])))
Make_Model_Name = tf.feature_column.embedding_column(Make_Model_Name, len(set(X['Make_Model_Name'])))
Flight_Plan = tf.feature_column.embedding_column(Flight_Plan, len(set(X['Flight_Plan'])))
Mission = tf.feature_column.embedding_column(Mission, len(set(X['Mission'])))
Flight_Phase1 = tf.feature_column.embedding_column(Flight_Phase1, len(set(X['Flight_Phase1'])))
Route_In_Use = tf.feature_column.embedding_column(Route_In_Use, len(set(X['Route_In_Use'])))
Airspace = tf.feature_column.embedding_column(Airspace, len(set(X['Airspace'])))

## Component
Aircraft_Component = tf.feature_column.embedding_column(Aircraft_Component, len(set(X['Aircraft_Component'])))
Manufacturer = tf.feature_column.embedding_column(Manufacturer, len(set(X['Manufacturer'])))

## Person
Location_Of_Person = tf.feature_column.embedding_column(Location_Of_Person, len(set(X['Location_Of_Person'])))
Location_In_Aircraft = tf.feature_column.embedding_column(Location_In_Aircraft, len(set(X['Location_In_Aircraft'])))
Reporter_Organization = tf.feature_column.embedding_column(Reporter_Organization, len(set(X['Reporter_Organization'])))
Function = tf.feature_column.embedding_column(Function, len(set(X['Function'])))
Qualification = tf.feature_column.embedding_column(Qualification, len(set(X['Qualification'])))
Human_Factors = tf.feature_column.embedding_column(Human_Factors, len(set(X['Human_Factors'])))

## Events
Anomaly = tf.feature_column.embedding_column(Anomaly, len(set(X['Anomaly'])))
Detector = tf.feature_column.embedding_column(Detector, len(set(X['Detector'])))
When_Detected = tf.feature_column.embedding_column(When_Detected, len(set(X['When_Detected'])))
Were_Passengers_Involved_In_Event = tf.feature_column.embedding_column(Were_Passengers_Involved_In_Event,
                                                                       len(set(X['Were_Passengers_Involved_In_Event'])))

## Assessments
Contributing_Factors_Situations = tf.feature_column.embedding_column(Contributing_Factors_Situations,
                                                                     len(set(X['Contributing_Factors_Situations'])))
Primary_Problem = tf.feature_column.embedding_column(Primary_Problem, len(set(X['Primary_Problem'])))


## Topic Mining from Accident Synopsis
word_1 = tf.feature_column.embedding_column(word_1, len(unique_topic_words))
word_2 = tf.feature_column.embedding_column(word_2, len(unique_topic_words))
word_3 = tf.feature_column.embedding_column(word_3, len(unique_topic_words))
word_4 = tf.feature_column.embedding_column(word_4, len(unique_topic_words))
word_5 = tf.feature_column.embedding_column(word_5, len(unique_topic_words))
word_6 = tf.feature_column.embedding_column(word_6, len(unique_topic_words))

## Build a neural network-based learning model

In [ ]:
from sklearn.model_selection import train_test_split
X_sub = X[['Locale_Reference', 'State_Reference', 'Flight_Conditions', 'Weather_Elements_Visibility', 
            'Work_Environment_Factor', 'Light', 'ATC_Advisory', 'Aircraft_Operator', 'Make_Model_Name', 
            'Crew_Size', 'Flight_Plan', 'Mission', 'Flight_Phase1',
            'Route_In_Use','Airspace', 'Aircraft_Component', 'Manufacturer', 'Location_Of_Person', 'Location_In_Aircraft',
            'Reporter_Organization', 'Function', 'Qualification', 'Human_Factors', 'Anomaly', 'Detector', 'When_Detected',
            'Were_Passengers_Involved_In_Event', 'Contributing_Factors_Situations', 'Primary_Problem',
            'word_1', 'word_2', 'word_3', 'word_4', 'word_5', 'word_6']]

X_train, X_test, Y_train, Y_test = train_test_split(X_sub, Y, test_size = 0.2, random_state = 101)

In [ ]:
## define input function
input_func = tf.estimator.inputs.pandas_input_fn(x = X_train, y = Y_train, batch_size = 500, 
                                                num_epochs = 2000, shuffle = True)

## define the feature columns
feat_cols = [Locale_Reference, State_Reference, Flight_Conditions, Weather_Elements_Visibility, Work_Environment_Factor, 
             Light, ATC_Advisory, Aircraft_Operator, Make_Model_Name, Crew_Size, Flight_Plan, Mission, Flight_Phase1, 
             Route_In_Use, Airspace, Aircraft_Component, Manufacturer, Location_Of_Person, Location_In_Aircraft, 
             Reporter_Organization, Function, Qualification, Human_Factors, Anomaly, Detector, When_Detected, 
             Were_Passengers_Involved_In_Event, Contributing_Factors_Situations, Primary_Problem]

## build the model
model = tf.estimator.DNNClassifier(hidden_units = [40, 40, 40, 40, 40, 40, 40, 40], feature_columns = feat_cols,
                                   n_classes = n_classes, optimizer = tf.train.AdamOptimizer(learning_rate = 0.001))

## train the model
model.train(input_fn = input_func, steps = 5000)

## Test the performance of the trained model

In [ ]:
eval_input = tf.estimator.inputs.pandas_input_fn(x = X_test, shuffle = False)
prediction = list(model.predict(eval_input))

pred_label = [int(pred['class_ids']) for pred in prediction]

from sklearn.metrics import classification_report
target_names = [str(i) for i in range(1, n_classes)]
print(classification_report(Y_test, pred_label, target_names=target_names))